In [50]:
import sys
sys.path.append('..')

import numpy as np
import socnet as sn

In [51]:
sn.graph_width = 500
sn.graph_height = 500
sn.node_size = 10
sn.edge_width = 1
sn.edge_color = (192, 192, 192)
sn.node_label_position = 'top center'

In [52]:
total_nodes = 200
percentage_portuguese = 0.05
percentage_native = 1 - percentage_portuguese

g = sn.generate_empty_graph(total_nodes)

In [53]:
from random import randint


for n in range(int(total_nodes * percentage_portuguese)):
    g.node[n]['nationality'] = 'portuguese'
    g.node[n]['color'] = (255,255,0)
    g.node[n]['label'] = n
    g.node[n]['population'] = randint(20, 50)
    
for n in range(int(total_nodes * percentage_portuguese),
               total_nodes):
    g.node[n]['nationality'] = 'native'
    g.node[n]['color'] = (255,0,255)
    g.node[n]['label'] = n
    g.node[n]['population'] = randint(40, 200)


In [54]:
from random import randint, choice

N = 50  # 1/50 chance of a node being connected to another

for n in g.nodes():
    for i in g.nodes():
        if n != i and randint(0, N) == 0:
            g.add_edge(n,i)
            g.edges[(n, i)]['label'] = choice(['+', '-'])

In [55]:
sn.reset_edge_colors(g)
sn.reset_positions(g)
sn.show_graph(g, nlab=True)

In [56]:
from random import choice, randint


def portuguese_vs_native(g, n0, n1):
    '''
    returns true if the first one is pt 
    and the second one is a native 
    '''
    return (g.node[n0]['nationality'] == 'portuguese' and \
            g.node[n1]['nationality'] == 'native')

def calculate_win_chance(g, n0, n1):
    '''
    returns the win chance of a node
    '''
    # Equation: w1*t1 + w2*t2 + ...
    #           -------------------
    #              w1 + w2 + ...
    
    # Terms:
    #    [0] - being a portuguese
    #    [1] - population proportion
    n_t = 2
    t = [0] * n_t
    w = [0] * n_t
    
    t[0] = 0.7
    w[0] = 1
    
    t[1] = g.node[n0]['population'] / (g.node[n0]['population'] + g.node[n1]['population'])
    w[1] = 0.5
    
    # Calculate
    return sum(x*y for x, y in zip(a, b)) / sum(w)

def fight(g, n0, n1):
    '''
    returns the looser of a simulated fight
    '''    
    P = calculate_win_chance(g, n0 n1)
    if g.node[n0]['nationality'] == g.node[n1]['nationality']:
        return choice([n0, n1])
    elif portuguese_vs_native(g, n0, n1):
        return n1 if randint(1, 10) > P else n0
    elif portuguese_vs_native(g, n1, n0):
        return n0 if randint(1, 10) > P else n1
    else:
        return -1  # error

In [57]:
from random import randint


def _remove_lone_nodes(g):
    remove = set()
    for n in g.nodes():
        if len(list(g.neighbors(n))) == 0:
            remove.add(n)
            
    g.remove_nodes_from(remove)


def iteration(g):
    # TODO: Implement population growth
    P = 1  # 10% chance a '-' edge will fight
    remove = set()
    for n, m in g.edges():
        if g.edges[n, m]['label'] == '-' and randint(1, 10) <= P:
            l = fight(g, n, m)
            remove.add(l)
    
    g.remove_nodes_from(remove)
    _remove_lone_nodes(g)

In [58]:
def snapshot(g, frames):
    frame = sn.generate_frame(g)
    frames.append(frame)

In [59]:
frames = []

for _ in range(30):
    iteration(g)
#     sn.reset_positions(g)
    snapshot(g, frames)
    
sn.show_animation(frames)

In [60]:
pt = 0
nt = 0

for n in g.nodes():
    if g.node[n]['nationality'] == 'portuguese':
        pt += 1
    else:
        nt += 1
        
print('''
    portuguese: {:2d} -- {:.2f}%
    native:     {:2d} -- {:.2f}%
'''.format(pt, (pt / (pt + nt)) * 100, 
           nt, (nt / (pt + nt)) * 100))


    portuguese:  5 -- 7.46%
    native:     62 -- 92.54%

